In [1]:
# Import python libraries
#
import numpy as np
import importlib
import pickle
import os
import plotly.express as px
import torch
from pprint import pprint
from collections import defaultdict
import pandas as pd

# Go one directory back, because all imports are done 
# relative to the root of the project.
#
if 'change_directory_to_root' not in globals():
    change_directory_to_root = True
    project_root = '..'
    os.chdir(project_root)

# Imports own modules.
#
import scripts.Visualization as Visualization
import scripts.ModelTrainer as ModelTrainer
import scripts.Utils as utils
import scripts.Simulation_config as Simulation_config
import scripts.Model as model


/home/molu/miniconda3/envs/xlstm/lib/python3.11/site-packages/torch/cuda/__init__.py:141: UserWarning: CUDA initialization: The NVIDIA driver on your system is too old (found version 11040). Please update your GPU driver by downloading and installing a new version from the URL: http://www.nvidia.com/Download/index.aspx Alternatively, go to: https://pytorch.org to install a PyTorch version that has been compiled with your version of the CUDA driver. (Triggered internally at /opt/conda/conda-bld/pytorch_1704987288773/work/c10/cuda/CUDAFunctions.cpp:108.)
  return torch._C._cuda_getDeviceCount() > 0
No CUDA runtime is found, using CUDA_HOME='/home/molu/miniconda3/envs/xlstm'


In [2]:
# Run the whole simulation
#
importlib.reload(model)
importlib.reload(ModelTrainer)
importlib.reload(Simulation_config)

train_all_models = False
if train_all_models:
    ModelTrainer.ModelTrainer().run()


In [26]:
# Print the sumarized simulation results (opionally for latex)
#

importlib.reload(utils)

all_train_histories = utils.Deserialize.get_training_histories('scripts/outputs/all_train_histories.pkl')

# Create a nested dictionary of the results
result_per_config = defaultdict(lambda: defaultdict(lambda: defaultdict(dict)))
for key, value in all_train_histories.items():
    model_types = key[0]
    load_profiles = key[1]
    sim_config = key[2]
    loss = value
    result_per_config[sim_config][model_types][load_profiles] = loss

# Calculate and print median and standard deviation for each config and model_type
for config, result_per_model in result_per_config.items():
    pprint(f'Configuration: {config}')
    print_for_latex = True
    latex_string = ''
    
    for model_type, result_per_profile in result_per_model.items():
        
        # Get al list of all losses of the current config and modeltype
        train_losses, test_MAE, test_MAPE  = [], [], []
        for load_profiles, results in result_per_profile.items():
            train_losses.append(float(results['loss'][-1]))
            test_MAE.append(float(results['test_loss'][-1]))
            test_MAPE.append(float(results['test_MAPE'][-1]))
        
        assert len(train_losses) == config.nrOfComunities
        assert len(test_MAE) == config.nrOfComunities
        assert len(test_MAPE) == config.nrOfComunities
        
        decimal_points_MAE = 4
        decimal_points_MAPE = 2
        mean_test_MAE = f'{np.mean(test_MAE):.{decimal_points_MAE}f}'
        mean_test_MAPE = f'{np.mean(test_MAPE):.{decimal_points_MAPE}f}'
        std_dev_test_MAE = f'{np.std(test_MAE):.{decimal_points_MAE}f}'
        std_dev_test_MAPE = f'{np.std(test_MAPE):.{decimal_points_MAPE}f}'
        mean_train_MAE = f'{np.mean(train_losses):.{decimal_points_MAE}f}'

        if print_for_latex:
            latex_string += f' & {mean_test_MAE}'
        else:
            # Print the results of the current config and modeltype
            print(f'    Model: {model_type}')
            print(f'      Mean Test MAE: {mean_test_MAE}')
            print(f'      Mean Test MAPE: {mean_test_MAPE}')
            print(f'      Standard Deviation Test MAE: {std_dev_test_MAE}')
            print(f'      Standard Deviation Test MAPE: {std_dev_test_MAPE}')
            print(f'      Mean Train MAE: {mean_train_MAE}\n')

    if print_for_latex == True:
        print(f'Latex Summary for this Configuration: {latex_string}')


("Configuration: Config_of_one_run(modelSize='MEDIUM', doPretraining=True, "
 'doTransferLearning=True, '
 "aggregation_Count='data/london_loadprofiles_74households_each.pkl', "
 'nrOfComunities=20, trainingHistory=466, modelInputHistory=24, '
 "usedModels=('KNN', 'PersistencePrediction', 'xLSTM', 'LSTM', 'Transformer'), "
 'epochs=100)')
Latex Summary for this Configuration:  & 0.3904 & 0.5081 & 0.2879 & 0.2925 & 0.3026
("Configuration: Config_of_one_run(modelSize='SMALL', doPretraining=True, "
 'doTransferLearning=True, '
 "aggregation_Count='data/london_loadprofiles_74households_each.pkl', "
 'nrOfComunities=20, trainingHistory=466, modelInputHistory=24, '
 "usedModels=('KNN', 'PersistencePrediction', 'xLSTM', 'LSTM', 'Transformer'), "
 'epochs=100)')
Latex Summary for this Configuration:  & 0.3904 & 0.5081 & 0.2951 & 0.2893 & 0.2978
("Configuration: Config_of_one_run(modelSize='LARGE', doPretraining=True, "
 'doTransferLearning=True, '
 "aggregation_Count='data/london_loadprofiles_

In [22]:
# Plot the losses over the training.
# (To see, if the models are trained stable.)
#

# Target config(s) to plot
plot_only_single_config = False
if plot_only_single_config:
    plotted_config = Simulation_config.configs[0]
    print(f"Plotted Config:")
    pprint(f"{plotted_config}")
filtered_train_histories = dict(
    (key, value) for key, value in all_train_histories.items() 
    if plot_only_single_config == False or key[2] == plotted_config
)

# Create a combined list of loss values and corresponding run names
combined_loss_data = []
for run_id, history in filtered_train_histories.items():
    
    # Define the labels of the following graph
    model_type, load_profile, act_config = run_id
    label = (model_type, load_profile, act_config.modelSize)    
    combined_loss_data.extend([(label, epoch + 1, loss) for epoch, loss in enumerate(history['loss'])])

# Create a DataFrame from the combined loss data
df = pd.DataFrame(combined_loss_data, columns=['Run', 'Epoch', 'Loss'])

# Use plotly express to plot the scatter graph
fig = px.scatter(df, x='Epoch', y='Loss', color='Run', 
                 labels={'Loss': 'Training RMSE Loss', 'Epoch': 'Epoch'},
                 title='Training Loss Over Epochs for Different Runs')
fig.update_yaxes(range=[0, 1])
fig.update_traces(marker=dict(size=5))
fig.update_layout(showlegend=False)
fig.show()


In [5]:
# Evaluate detailed power profiles
#

importlib.reload(Visualization)
importlib.reload(model)
importlib.reload(utils)

test_profile = "scripts/outputs/file_0.pkl"
with open(test_profile, 'rb') as f:
    (X, Y, modelAdapter) = pickle.load(f)

path_to_trained_parameters = 'scripts/outputs/all_trained_models.pth'
model_type = 'PersistencePrediction'
config_id = 0    
myModel = utils.Deserialize.get_trained_model(path_to_trained_parameters, model_type, test_profile, config_id, modelAdapter)
plotlyApp = Visualization.PlotlyApp(X, Y, myModel, modelAdapter, None, 'UTC+00:00')
plotlyApp.run(myport=8056)


In [6]:
# Print the model parameter sizes
#

importlib.reload(model)

model_types = ['xLSTM', 'LSTM', 'Transformer']
for model_type in model_types:
    for model_size in ['SMALL', 'MEDIUM', 'LARGE']:

        # Test, if the model is run-able
        num_of_features = 18
        m = model.Model(model_type, model_size, num_of_features)
        x = torch.zeros((7, 24*22, num_of_features))
        m.my_model(x)

        # Print the model's parameter count
        nr_of_parameters = m.get_nr_of_parameters(do_print=False)
        print(f"{model_type} - {model_size} has {nr_of_parameters} parameters.")


xLSTM - SMALL has 19791 parameters.
xLSTM - MEDIUM has 26411 parameters.
xLSTM - LARGE has 97679 parameters.
LSTM - SMALL has 17463 parameters.
LSTM - MEDIUM has 44031 parameters.
LSTM - LARGE has 104831 parameters.
Transformer - SMALL has 24423 parameters.
Transformer - MEDIUM has 50863 parameters.
Transformer - LARGE has 113351 parameters.
